# Crystal Case Study

## Setup

In [93]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import seaborn as sns
import datetime
import warnings

In [94]:
warnings.filterwarnings("ignore")

In [95]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


## Import data

In [96]:
df = pd.read_csv('/content/drive/Shareddrives/Crystal Course/Project/Automotive_1.csv')

In [97]:
df

datecrawled  \
0       2016-03-24T11:52:17   
1       2016-03-24T10:58:45   
2       2016-03-14T12:52:21   
3       2016-03-17T16:54:04   
4       2016-03-31T17:25:20   
...                     ...   
199995  2016-03-27T07:57:15   
199996  2016-03-07T15:47:49   
199997  2016-04-03T11:43:48   
199998  2016-04-02T01:54:47   
199999  2016-03-23T10:57:06   

                                                     name  seller offertype  \
0                                              Golf_3_1.6  privat   Angebot   
1                                    A5_Sportback_2.7_Tdi  privat   Angebot   
2                          Jeep_Grand_Cherokee_"Overland"  privat   Angebot   
3                                       GOLF_4_1_4__3T?ER  privat   Angebot   
4                          Skoda_Fabia_1.4_TDI_PD_Classic  privat   Angebot   
...                                                   ...     ...       ...   
199995  Fiat_Stilo_Active_viele_Extras_wenig_km_Rentne...  privat   Angebot   
199996                                           BMW_318i  privat   Angebot   
199997                                    Ford_Fiesta_1.4  privat   Angebot   
199998                                Nissan_Qashqai__AHK  privat   Angebot   
199999            Golf_4_Automatik_Top_Auto_von_Rentrerin  privat   Angebot   

        price   abtest vehicletype yearofregistration    gearbox powerps  \
0         480     test         NaN               1993     manual       0   
1       18300     test       coupe               2011     manual     190   
2        9800     test         suv               2004  automatik     163   
3        1500     test  kleinwagen               2001     manual      75   
4        3600     test  kleinwagen               2008     manual      69   
...       ...      ...         ...                ...        ...     ...   
199995   2490     test   limousine               2002     manual      80   
199996    600  control   limousine               1998     manual     116   
199997   3900  control  kleinwagen               2008     manual      80   
199998  11400     test         suv               2012     manual     110   
199999   1600  control  kleinwagen               1998  automatik     101   

          model  kilometer monthofregistration fueltype       brand  \
0          golf     150000                   0   benzin  volkswagen   
1           NaN     125000                   5   diesel        audi   
2         grand     125000                   8   diesel        jeep   
3          golf     150000                   6   benzin  volkswagen   
4         fabia      90000                   7   diesel       skoda   
...         ...        ...                 ...      ...         ...   
199995    stilo      70000                   2   benzin        fiat   
199996      3er     150000                   3   benzin         bmw   
199997   fiesta      90000                   2   benzin        ford   
199998  qashqai     125000                   3   diesel      nissan   
199999     golf     150000                   5   benzin  volkswagen   

       notrepaireddamage          datecreated nrofpictures postalcode  \
0                    NaN  2016-03-24T00:00:00        FALSE      70435   
1                    yes  2016-03-24T00:00:00        FALSE      66954   
2                    NaN  2016-03-14T00:00:00        FALSE      90480   
3                     no  2016-03-17T00:00:00        FALSE      91074   
4                     no  2016-03-31T00:00:00        FALSE      60437   
...                  ...                  ...          ...        ...   
199995               NaN  2016-03-27T00:00:00        FALSE      21073   
199996                no  2016-03-07T00:00:00        FALSE      26340   
199997                no  2016-04-03T00:00:00        FALSE      90431   
199998                no  2016-04-01T00:00:00        FALSE      49536   
199999                no  2016-03-23T00:00:00        FALSE      32689   

                   lastseen  
0       2016-04-07T03

## Data cleaning

### Fix dataset column offset

In [98]:
# Shift DataFrame
index_to_shift = df[df['name'].str.contains('?privat', regex=False)].index

rows_not_shift = df.iloc[index_to_shift,:2] 
rows_to_shift = df.iloc[index_to_shift,2:].shift(1,axis=1)

df.iloc[index_to_shift,:] = pd.concat([rows_not_shift, rows_to_shift], axis=1)
df.iloc[index_to_shift,:].head()

datecrawled                                 name seller  \
1409  2016-03-24T14:54:19                     Audi_Coup?privat    NaN   
4469  2016-03-05T15:53:26               Mercedes_C_Coup?privat    NaN   
5140  2016-03-24T10:36:18                 BMW_123d_Coup?privat    NaN   
5297  2016-04-05T00:56:17       Ford_Focus_MK1_1.6_coup?privat    NaN   
5411  2016-03-17T14:49:23  BMW_e30_Karosse_2Tuerer_Coup?privat    NaN   

     offertype  price   abtest vehicletype yearofregistration gearbox powerps  \
1409   Angebot   2000     test       coupe               1990  manual     113   
4469   Angebot   5250  control       coupe               2003  manual     143   
5140   Angebot  12500     test       coupe               2008  manual     204   
5297   Angebot   1700  control       coupe               2003  manual     101   
5411   Angebot    199  control         NaN               1990  manual      99   

         model kilometer monthofregistration fueltype          brand  \
1409    andere    150000                   9   benzin           audi   
4469  c_klasse    150000                   3   benzin  mercedes_benz   
5140       1er    150000                   9   diesel            bmw   
5297     focus    150000                   0   benzin           ford   
5411       3er    150000                   3   benzin            bmw   

     notrepaireddamage          datecreated nrofpictures postalcode  \
1409               yes  2016-03-24T00:00:00        FALSE      85077   
4469                no  2016-02-28T00:00:00        FALSE      49661   
5140               NaN  2016-03-24T00:00:00        FALSE      81673   
5297               NaN  2016-04-05T00:00:00        FALSE      66773   
5411               yes  2016-03-17T00:00:00        FALSE      85764   

                 lastseen  
1409  2016-04-07T07:17:26  
4469  2016-04-04T19:46:58  
5140  2016-04-07T01:46:48  
5297  2016-04-07T03:46:09  
5411  2016-03-20T16:17:36

In [99]:
# Clean column name
df['name'] = list(map(lambda x: x.replace('?privat',''), df['name']))

### Drop columns

In [100]:
df['seller'].value_counts()

privat        199827
gewerblich         3
Name: seller, dtype: int64

In [101]:
df['nrofpictures'].value_counts()

FALSE    200000
Name: nrofpictures, dtype: int64

In [102]:
df['offertype'].value_counts()

Angebot    199994
Gesuch          6
Name: offertype, dtype: int64

In [103]:
df = df.drop(columns = ['name', 'seller', 'nrofpictures', 'offertype'])

In [104]:
df.head()

datecrawled  price abtest vehicletype yearofregistration  \
0  2016-03-24T11:52:17    480   test         NaN               1993   
1  2016-03-24T10:58:45  18300   test       coupe               2011   
2  2016-03-14T12:52:21   9800   test         suv               2004   
3  2016-03-17T16:54:04   1500   test  kleinwagen               2001   
4  2016-03-31T17:25:20   3600   test  kleinwagen               2008   

     gearbox powerps  model kilometer monthofregistration fueltype  \
0     manual       0   golf    150000                   0   benzin   
1     manual     190    NaN    125000                   5   diesel   
2  automatik     163  grand    125000                   8   diesel   
3     manual      75   golf    150000                   6   benzin   
4     manual      69  fabia     90000                   7   diesel   

        brand notrepaireddamage          datecreated postalcode  \
0  volkswagen               NaN  2016-03-24T00:00:00      70435   
1        audi               yes  2016-03-24T00:00:00      66954   
2        jeep               NaN  2016-03-14T00:00:00      90480   
3  volkswagen                no  2016-03-17T00:00:00      91074   
4       skoda                no  2016-03-31T00:00:00      60437   

              lastseen  
0  2016-04-07T03:16:57  
1  2016-04-07T01:46:50  
2  2016-04-05T12:47:46  
3  2016-03-17T17:40:17  
4  2016-04-06T10:17:21

### Variable types

In [105]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 200000 entries, 0 to 199999
Data columns (total 16 columns):
 #   Column               Non-Null Count   Dtype 
---  ------               --------------   ----- 
 0   datecrawled          200000 non-null  object
 1   price                200000 non-null  object
 2   abtest               200000 non-null  object
 3   vehicletype          179622 non-null  object
 4   yearofregistration   200000 non-null  object
 5   gearbox              189151 non-null  object
 6   powerps              200000 non-null  object
 7   model                188883 non-null  object
 8   kilometer            200000 non-null  object
 9   monthofregistration  200000 non-null  object
 10  fueltype             181917 non-null  object
 11  brand                200000 non-null  object
 12  notrepaireddamage    161149 non-null  object
 13  datecreated          200000 non-null  object
 14  postalcode           200000 non-null  object
 15  lastseen             200000 non-nu

### Nans Bar Chart

In [106]:
nans = {}
for i in df.columns:
  nans[i] = df[i].isna().sum()

nans = pd.Series(nans, name='Nans Count')

In [107]:
fig = px.bar(nans, orientation='h')
fig.show()

## Cleaning the Data

In [108]:
df = df.dropna(axis = 0, how = 'any')

In [109]:
df

datecrawled  price   abtest vehicletype yearofregistration  \
3       2016-03-17T16:54:04   1500     test  kleinwagen               2001   
4       2016-03-31T17:25:20   3600     test  kleinwagen               2008   
5       2016-04-04T17:36:23    650     test   limousine               1995   
6       2016-04-01T20:48:51   2200     test      cabrio               2004   
7       2016-03-21T18:54:38      0     test   limousine               1980   
...                     ...    ...      ...         ...                ...   
199994  2016-03-06T13:43:01   2199  control  kleinwagen               2001   
199996  2016-03-07T15:47:49    600  control   limousine               1998   
199997  2016-04-03T11:43:48   3900  control  kleinwagen               2008   
199998  2016-04-02T01:54:47  11400     test         suv               2012   
199999  2016-03-23T10:57:06   1600  control  kleinwagen               1998   

          gearbox powerps    model kilometer monthofregistration fueltype  \
3          manual      75     golf    150000                   6   benzin   
4          manual      69    fabia     90000                   7   diesel   
5          manual     102      3er    150000                  10   benzin   
6          manual     109  2_reihe    150000                   8   benzin   
7          manual      50   andere     40000                   7   benzin   
...           ...     ...      ...       ...                 ...      ...   
199994     manual      50    arosa    150000                   2   benzin   
199996     manual     116      3er    150000                   3   benzin   
199997     manual      80   fiesta     90000                   2   benzin   
199998     manual     110  qashqai    125000                   3   diesel   
199999  automatik     101     golf    150000                   5   benzin   

             brand notrepaireddamage          datecreated postalcode  \
3       volkswagen                no  2016-03-17T00:00:00      91074   
4            skoda                no  2016-03-31T00:00:00      60437   
5              bmw               yes  2016-04-04T00:00:00      33775   
6          peugeot                no  2016-04-01T00:00:00      67112   
7       volkswagen                no  2016-03-21T00:00:00      19348   
...            ...               ...                  ...        ...   
199994        seat                no  2016-03-06T00:00:00      61184   
199996         bmw                no  2016-03-07T00:00:00      26340   
199997        ford                no  2016-04-03T00:00:00      90431   
199998      nissan                no  2016-04-01T00:00:00      49536   
199999  volkswagen                no  2016-03-23T00:00:00      32689   

                   lastseen  
3       2016-03-17T17:40:17  
4       2016-04-06T10:17:21  
5       2016-04-06T19:17:07  
6       2016-04-05T18:18:39  
7       2016-03-25T16:47:58  
...                     ...  
199994  2016-03-17T15:18:03  
199996  2016-03-08T19:18:23  
199997  2016-04-07T12:45:00  
199998  2016-04-06T06:15:41  
199999  2016-03-30T20:17:10  

[140510 rows x 16 columns]

## Data Pre-processing

### Powerps

In [110]:
df['powerps'] = df['powerps'].astype(int)

In [111]:
df = df[(25 <= df['powerps']) & (df['powerps'] <= 600)]
df['powerps'] = pd.qcut(df['powerps'],q = 4,labels=[0,1,2,3])

### Kilometer

In [112]:
df['kilometer'] = df['kilometer'].astype(int)

In [113]:
km_list = list(df.kilometer.unique())
km_list.sort()

In [114]:
# Replace kilometer w with their corresponding value from [0,1,2,3...]
df['kilometer'] = df['kilometer'].replace(km_list,list(range(len(km_list))))

### Month of registration

In [115]:
df['monthofregistration'] = df['monthofregistration'].astype(int)

### Price

In [116]:
df['price'] = df['price'].astype(float)

In [117]:
# Drop the rows where the price is not between $1,750 - $50,000
df = df[(1750 <= df['price']) & ( df['price'] <= 50000)]

In [118]:
df['price'].describe()

count    98672.000000
mean      8539.621909
std       7380.880808
min       1750.000000
25%       3390.000000
50%       5999.000000
75%      11000.000000
max      50000.000000
Name: price, dtype: float64

### Year of registration

In [119]:
df['yearofregistration'] = df['yearofregistration'].astype(int)

In [120]:
# Drop the rows where the year of registration is below 1990
df = df[df['yearofregistration'] > 1990]

In [121]:
px.histogram(df['yearofregistration'],
             title = 'Histogram Year of Registration')

### Not repaired damage

In [122]:
df['notrepaireddamage'].unique()

array(['no', 'yes'], dtype=object)

In [123]:
px.histogram(df['notrepaireddamage'],
             title = 'Histogram of cars with unrepaired damages')

In [124]:
dict_damage = {'yes': 1, 'no': 0}
df['notrepaireddamage'] = df['notrepaireddamage'].replace(dict_damage)

### Brand

In [125]:
top_brands = df.brand.value_counts()
px.bar(top_brands, orientation='h', title = 'Histogram Car Brands')

In [126]:
# dict_brand = dict(enumerate(df['brand'].unique()))
# # Corrección
# dict_brand = {brand: num for num, brand in dict_brand.items()}
# df['brand'] = df['brand'].replace(dict_brand)

### Model

In [127]:
top_models = df.model.value_counts().iloc[:20]
px.bar(top_models, orientation='h', title = 'Top 20 most popular models')

In [128]:
# dict_model = dict(enumerate(df['model'].unique()))
# # Corrección
# dict_model = {model: num for num, model in dict_model.items()}
# df['model'] = df['model'].replace(dict_model)
# df['model']

### Vehicle type

In [129]:
top_type = df.vehicletype.value_counts()
px.bar(top_type, orientation='h', title = 'Histogram Vehicle Type')

In [130]:
dict_vehicletype = dict(enumerate(df['vehicletype'].unique()))
dict_vehicletype = {vehicle: num for num, vehicle in dict_vehicletype.items()}
df['vehicletype'] = df['vehicletype'].replace(dict_vehicletype)

### Gearbox

In [131]:
px.histogram(df['gearbox'], title = 'Histogram Gearbox')

In [132]:
dict_gearbox = dict(enumerate(df['gearbox'].unique()))
dict_gearbox = {gearbox: num for num, gearbox in dict_gearbox.items()}
df['gearbox'] = df['gearbox'].replace(dict_gearbox)

### Fuel type

In [133]:
px.histogram(df['fueltype'], title = 'Histogram fuel type')

In [134]:
dict_fueltype = dict(enumerate(df['fueltype'].unique()))
dict_fueltype = {fueltype: num for num, fueltype in dict_fueltype.items()}
df['fueltype'] = df['fueltype'].replace(dict_fueltype)

### Dates

In [135]:
df2 = df.copy()

In [136]:
df2.head(5)

datecrawled    price   abtest  vehicletype  yearofregistration  \
4   2016-03-31T17:25:20   3600.0     test            0                2008   
6   2016-04-01T20:48:51   2200.0     test            1                2004   
10  2016-03-26T19:54:18   2000.0  control            2                2004   
11  2016-04-07T10:06:22   2799.0  control            3                2005   
14  2016-03-21T12:57:01  17999.0  control            4                2011   

    gearbox powerps    model  kilometer  monthofregistration  fueltype  \
4         0       0    fabia          9                    7         0   
6         0       1  2_reihe         12                    8         1   
10        0       1  3_reihe         12                   12         1   
11        0       2   passat         12                   12         0   
14        0       3   navara          7                    3         0   

         brand  notrepaireddamage          datecreated postalcode  \
4        skoda                  0  2016-03-31T00:00:00      60437   
6      peugeot                  0  2016-04-01T00:00:00      67112   
10       mazda                  0  2016-03-26T00:00:00      96224   
11  volkswagen                  1  2016-04-07T00:00:00      57290   
14      nissan                  0  2016-03-21T00:00:00       4177   

               lastseen  
4   2016-04-06T10:17:21  
6   2016-04-05T18:18:39  
10  2016-04-06T10:45:34  
11  2016-04-07T10:25:17  
14  2016-04-06T07:45:42

In [137]:
# Convert to datetime format
df2.lastseen = pd.to_datetime(df2['lastseen'])
df2.datecreated = pd.to_datetime(df2['datecreated'])
df2.datecrawled = pd.to_datetime(df2['datecrawled'])

In [138]:
print("DATE CREATED - DATECRAWLED")
print((df2.datecreated - df2.datecrawled ).describe())

DATE CREATED - DATECRAWLED
count                          96306
mean     -1 days +05:38:55.843748054
std        2 days 07:06:13.795585487
min              -370 days +09:17:14
25%                -1 days +03:17:09
50%                -1 days +07:06:03
75%                -1 days +11:02:27
max                -1 days +23:34:44
dtype: object


There is no last seen dates before crawled dates (for obvious reasons).
What happens with vehicles whose creation date is earlier than
its crawled date and sold before the crawl started?
The crawl never registers its last seen which is interpreted as never being sold.
* Option 1: Those sold before the crawl have their datecreate deleted and then there would be no problem -> OK
* Option 2: We do not know if it was sold or not and the last seen date is the last date of the crawl and it is considered as not sold. -> bad

Solution: Throw away all the ones that have been created before the first crawled date
* Rows dropped: 2721

In [139]:
len(df2)

96306

In [140]:
# Make sure the datacreated after when the crawler started
# The trace will always be after the creation date, so each time this line is
# executed, more data will be deleted, it will be deleted day by day.
df2 = df2[df2['datecreated'] >= df2['datecrawled'].min()]

In [141]:
# Comparison
fig = go.Figure()

fig.add_trace(go.Histogram(x=df2['lastseen'].dt.date, name = 'LastSeen'))
fig.add_trace(go.Histogram(x=df2['datecrawled'].dt.date, name = 'Crawled'))
fig.add_trace(go.Histogram(x=df2['datecreated'].dt.date, name = 'Created'))
fig.update_layout(barmode='group')

In [142]:
len(df2)

93585

In [143]:
# Remove those that were crawled within the last 3 days, it is not right to
# consider them as unsold if the ad was created at the last moment
df2 = df2[df2['datecrawled'] < pd.to_datetime('2016-04-05')]
# df2 = df2[df2['datecreated'] < pd.to_datetime('2016-04-05')]

### Already sold

In [144]:
# We can say that if the date of the last time the database was crawled is
# greater than a certain date of last seen that vehicle was sold?
# -> We will proceed with this line of thought

In [145]:
df2.datecrawled.max()

Timestamp('2016-04-04 23:57:46')

In [146]:
# The rows that have a last seen earlier than when the crawl stopped,
# means that they were sold.
# Histogram of those rows
df2['alreadysold'] = (df2.lastseen < "2016-04-05T00:00:00").astype(int)
px.histogram(df2[df2['alreadysold'] == 1].lastseen, title = 'Histogram Car Sales')

In [147]:
df2['alreadysold'].value_counts()

0    49504
1    42434
Name: alreadysold, dtype: int64

### Time until sale

In [148]:
# Subtract LASTSEEN - DATECREATED to find the time to sell
# The values ​​with NaT is that they were not sold
df2['selltime'] = df2[df2.alreadysold == 1].lastseen - df2[df2.alreadysold == 1].datecreated
df2['selltime']

4                     NaT
6                     NaT
10                    NaT
14                    NaT
17                    NaT
               ...       
199980                NaT
199991   17 days 07:18:18
199994   11 days 15:18:03
199997                NaT
199998                NaT
Name: selltime, Length: 91938, dtype: timedelta64[ns]

In [149]:
df2.selltime.describe()

count                        42434
mean     6 days 03:26:38.778338125
std      5 days 20:59:22.424196546
min                0 days 00:36:25
25%         1 days 11:16:45.500000
50%                4 days 05:16:29
75%         9 days 01:45:32.500000
max               29 days 23:45:35
Name: selltime, dtype: object

In [150]:
# Of the cars sold, HISTOGRAM of their sale time in days
px.histogram(df2[df2['alreadysold'] == 1].selltime.apply(lambda x : x.days))

# Implementación del modelo

In [151]:
import sklearn
from sklearn.tree import DecisionTreeClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix
from sklearn.model_selection import GridSearchCV

## Data Split

In [152]:
X = df2[['gearbox', 'price', 'brand', 'kilometer', 'fueltype', 'yearofregistration']]
y = df2['alreadysold']

In [153]:
dummies_gearbox = pd.get_dummies(X['gearbox'])
dummies_brand = pd.get_dummies(X['brand'])
dummies_fueltype = pd.get_dummies(X['fueltype'])
dummies_yearofregistration = pd.get_dummies(X['yearofregistration'])

In [154]:
X = pd.concat([X[['price', 'kilometer', 'yearofregistration']], dummies_gearbox], axis = 1)

In [155]:
X.head(5)

price  kilometer  yearofregistration  0  1
4    3600.0          9                2008  1  0
6    2200.0         12                2004  1  0
10   2000.0         12                2004  1  0
14  17999.0          7                2011  1  0
17  18000.0          2                2007  0  1

In [156]:
y

4         0
6         0
10        0
14        0
17        0
         ..
199980    0
199991    1
199994    1
199997    0
199998    0
Name: alreadysold, Length: 91938, dtype: int64

In [157]:
X_train, X_test, y_train, y_test = train_test_split(
...     X, y, test_size=0.3, random_state=42)

## Decision Tree

In [158]:
dtc = DecisionTreeClassifier()
dtc.fit(X_train, y_train)

DecisionTreeClassifier()

In [159]:
from sklearn import tree

In [160]:
df2.vehicletype

4         0
6         1
10        2
14        4
17        2
         ..
199980    3
199991    7
199994    0
199997    0
199998    4
Name: vehicletype, Length: 91938, dtype: int64

In [161]:
# print(tree.export_text(dtc, feature_names = list(X.columns)))

In [162]:
preds = dtc.predict(X_test)
confusion_matrix(y_test, preds)

array([[9166, 5737],
       [6435, 6244]])

In [163]:
dtc.score(X_test, y_test)

0.5586977013994634

## Random Forest

In [164]:
from sklearn.ensemble import RandomForestClassifier

In [165]:
X

price  kilometer  yearofregistration  0  1
4        3600.0          9                2008  1  0
6        2200.0         12                2004  1  0
10       2000.0         12                2004  1  0
14      17999.0          7                2011  1  0
17      18000.0          2                2007  0  1
...         ...        ...                 ... .. ..
199980  12999.0          8                2011  1  0
199991   4900.0         12                1992  1  0
199994   2199.0         12                2001  1  0
199997   3900.0          9                2008  1  0
199998  11400.0         11                2012  1  0

[91938 rows x 5 columns]

In [166]:
rnd_for = RandomForestClassifier()

In [167]:
rnd_for.fit(X_train,y_train)

RandomForestClassifier()

In [168]:
preds = rnd_for.predict(X_test)

In [169]:
rnd_for.feature_importances_

array([0.77464131, 0.08848602, 0.13212355, 0.00244372, 0.00230539])

# XGB Booster

In [170]:
import xgboost as xgb

In [171]:
#param = {'max_depth':2, 'eta':1, 'objective':'binary:logistic' }

xgbc0 = xgb.XGBClassifier(objective='binary:logistic',
                          gamma='0.5',
                          learning_rate=0.01,
                          n_estimators=50,
                          booster='gbtree',
                          eval_metric='auc',
                          tree_method='hist',
                          grow_policy='lossguide',
                          use_label_encoder=False)
xgbc0.fit(X_train , y_train)

XGBClassifier(eval_metric='auc', gamma='0.5', grow_policy='lossguide',
              learning_rate=0.01, n_estimators=50, tree_method='hist',
              use_label_encoder=False)

In [172]:
default_params = {'gamma': [0,0.5, 1],
              'learning_rate': [0.01, 0.03, 0.06, 0.1, 0.25,  0.6],
              'n_estimators': [50,80,100,150]}

clf0 = GridSearchCV(estimator=xgbc0, scoring='accuracy', param_grid=default_params, return_train_score=True, verbose=1, cv=2)
clf0.fit(X_train, y_train.values.ravel())

# results dataframe
df = pd.DataFrame(clf0.cv_results_)

Fitting 2 folds for each of 72 candidates, totalling 144 fits


In [173]:
confusion_matrix(y_test, xgbc0.predict(X_test))

array([[10009,  4894],
       [ 6626,  6053]])

In [174]:
xgbc0.score(X_test, y_test)

0.5823363062867087